In [0]:
from pyspark.sql.types import *
from pyspark.sql.functions import *

In [0]:
df_raw = spark.read.json("dbfs:/FileStore/tables/SteamProject/steam_data.json")
df_raw.printSchema()

root
 |-- categories: array (nullable = true)
 |    |-- element: string (containsNull = true)
 |-- date: string (nullable = true)
 |-- developer: string (nullable = true)
 |-- full_desc: struct (nullable = true)
 |    |-- desc: string (nullable = true)
 |    |-- sort: string (nullable = true)
 |-- img_url: string (nullable = true)
 |-- name: string (nullable = true)
 |-- pegi: struct (nullable = true)
 |    |-- age_limit: string (nullable = true)
 |    |-- pegi_tags: array (nullable = true)
 |    |    |-- element: string (containsNull = true)
 |    |-- pegi_url: string (nullable = true)
 |-- popu_tags: array (nullable = true)
 |    |-- element: string (containsNull = true)
 |-- price: string (nullable = true)
 |-- publisher: string (nullable = true)
 |-- requirements: struct (nullable = true)
 |    |-- minimum: struct (nullable = true)
 |    |    |-- linux: struct (nullable = true)
 |    |    |    |-- graphics: string (nullable = true)
 |    |    |    |-- memory: string (nullable = tru

In [0]:
display(df_raw)

categories date developer full_desc img_url name pegi popu_tags price publisher requirements url_info List(Online PvPLAN, PvPOnline Co-opLAN, Co-opCross-Platform Multiplayer Remote, Play on, Phone Remote Play, on Tablet) Nov 16, 2018 Innersloth List(About This Game Play with 4-10 player online or via local WiFi as you attempt to prepare your spaceship for departure, but beware as one or more random players among the Crew are Impostors bent on killing everyone!Originally created as a party game, we recommend playing with friends at a LAN party or online using voice chat. Enjoy cross-platform play between Android, iOS and PC. Win by completing tasks to prepare the ship or ejecting all Impostors. React quickly to undo the Impostor's sabotages. Check the Admin map and Security cameras to keep tabs on other Crewmates. Report any dead bodies immediately to start discussion of who the suspected Impostor is. Call emergency meetings to discuss suspicious behavior. Vote to eject suspected Impostors. Kill crewmates and frame bystanders. Pretend to run tasks to blend in with the crewmates. Sneak through the vents to quickly move about the ship. Use sabotages to cause chaos and divide the crew. Close doors to trap victims and kill in private.Features Customization: Pick your color and hat. Lots of game options: Add more impostors, more tasks, and so much more! Quickly find a game online from the host list. In-game text chat. Rich discord integration. Cross-platform play between PC, Android, and iOS!, game) https://steamcdn-a.akamaihd.net/steam/apps/945360/header.jpg?t=1598556351 Among Us null List(Multiplayer, Online, Space, Social, Deduction, Survival, Funny2, Psychological, Local, Multiplayer, Cartoony, Casual, Indie, Colorful, Minigames, Local, Down, Aliens+) 499 Innersloth List(List(null, null, List(, 1 , Windows 7 SP1+, SSE2 instruction set support)), List(null, null, null)) List(945360, app, https://store.steampowered.com/app/945360/Among_Us/?snr=1_7_7_230_150_1, Among Us) List(Steam Achievements Full, controller supportSteam, Trading Cards Steam, Workshop In-App Purchases Valve, Anti-Cheat enabledStats Remote, Play on, Phone Remote Play, on Tablet Remote, Play on) Aug 21, 2012 Valve, Hidden Path Entertainment List(About This Game Counter-Strike: Global Offensive (CS: GO) expands upon the team-based action gameplay that it pioneered when it was launched 19 years ago.CS: GO features new maps, characters, weapons, and game modes, and delivers updated versions of the classic CS content (de_dust2, etc.)."Counter-Strike took the gaming industry by surprise when the unlikely MOD became the most played online PC action game in the world almost immediately after its release in August 1999," said Doug Lombardi at Valve. "For the past 12 years, it has continued to be one of the most-played games in the world, headline competitive gaming tournaments and selling over 25 million units worldwide across the franchise. CS: GO promises to expand on CS' award-winning gameplay and deliver it to gamers on the PC as well as the next gen consoles and the Mac.", game) https://steamcdn-a.akamaihd.net/steam/apps/730/header.jpg?t=1592263625 Counter-Strike: Global Offensive null List(Shooter, Multiplayer, Competitive, Action, Team-, Basede, Sports, Tactical, First-, Person, Online, Strategy, Military, Difficult, Trading, Realistic, Fast-, Paced, Moddable+) free Valve List(List(List( nVidia GeForce 8600/9600GT, ATI/AMD Radeon HD2600/3600 (Graphic Drivers: nVidia 310, AMD 12.11), OpenGL 2.1, 4 GB RAM, Ubuntu 12.04, 64-bit Dual core from Intel or AMD at 2.8 GHz), null, List( Video card must be 256 MB or more and should be a , 2 GB RAM, Windows® 7/Vista/XP, Intel® Core™ 2 Duo E6600 or AMD Phenom™ X3 8750 processor or better)), List(null, null, null)) List(730, app, https://store.steampowered.com/app/730/CounterStrike_Global_Offensive/?snr=1_7_7_230_150_1, CounterStrike Global Offensive) List(MMOOnline PvPOnline, Co-opSteam Achievements Full, controller supportIn-A

In [0]:

schema_games = StructType([
    StructField('url_info', StructType([
        StructField('id', StringType(), True),
        StructField('type', StringType(), True) 
    ]), True),
    StructField('name', StringType(), True),
    StructField('date', StringType(), True),
    StructField('developer', StringType(), True),
    StructField('publisher', StringType(), True),
    StructField('price', StringType(), True)
])

df_games = spark.read.json("dbfs:/FileStore/tables/SteamProject/steam_data.json",
                            schema=schema_games)

In [0]:

# Removendo dados null
df_games = df_games.where(df_games.url_info.isNotNull())

# Removendo dados null
df_games = df_games.where(df_games.developer.isNotNull())

In [0]:

# Desfazendo struct em novas colunas
df_games = df_games.select(
    '*',    # Faz manter as outras colunas 
    col('url_info.id').alias('id'),
).drop('url_info')

df_games = df_games.withColumn('date', 
    when(df_games.date.isNull(), lit('none'))
    .otherwise(df_games.date)
)

# Subistituindo valores null 
df_games = df_games.withColumn('publisher', 
    when(df_games.publisher.isNull(), lit('none'))
    .otherwise(df_games.publisher)
)

# Corrigindo valores ausentes
df_games = df_games.withColumn(
    'price',
    when(col('price') == '', None).otherwise(col('price'))
)

df_games = df_games.withColumn('price', 
    when(df_games.price.isNull(), lit('none'))
    .otherwise(df_games.price)
)

In [0]:

# Salvando csv
df_games.write.csv('/mnt/bronze/steam_games_bronze.csv',
                    mode='overwrite',
                    header=True)

In [0]:
 
schema_category = StructType([
    StructField('url_info', StructType([
        StructField('id', StringType(), True),
        StructField('type', StringType(), True) 
    ]), True),
    StructField('categories', ArrayType(StringType()), True)
])

df_category = spark.read.json("dbfs:/FileStore/tables/SteamProject/steam_data.json",
                            schema=schema_category)

In [0]:

# Removendo dados null
df_category = df_category.where(df_category.url_info.isNotNull())

# Desfazendo struct em novas colunas
df_category = df_category.select(
    '*',    # Faz manter as outras colunas 
    col('url_info.id').alias('id'),
).drop('url_info')

df_category = df_category.select(
    '*',    # Faz manter as outras colunas 
    col('categories').alias('category'),
).drop('categories')

In [0]:

# Concatenando o array
df_category = df_category.withColumn(
    'category',
    concat_ws(' | ', col('category'))
)

In [0]:
display(df_category)

id category 945360 Online PvPLAN | PvPOnline Co-opLAN | Co-opCross-Platform Multiplayer Remote | Play on | Phone Remote Play | on Tablet 730 Steam Achievements Full | controller supportSteam | Trading Cards Steam | Workshop In-App Purchases Valve | Anti-Cheat enabledStats Remote | Play on | Phone Remote Play | on Tablet Remote | Play on 1097150 MMOOnline PvPOnline | Co-opSteam Achievements Full | controller supportIn-App | Purchases Remote Play | on Phone Remote | Play on 1158310 Single-playerOnline PvPSteam | Achievements Steam Trading | Cards Steam Workshop Steam 1085660 Single-playerOnline PvPOnline | Co-opSteam Achievements Full | controller supportIn-App | Purchases Remote Play | on Phone Remote | Play on | Tablet Remote Play | on TVRequires | agreement to | a 3rd-party | EULADestiny 2 1145360 Single-playerFull controller | supportSteam Trading | Cards Captions availableSteam | Cloud Remote Play | on Phone Remote | Play on | Tablet Remote Play | on TV 1172620 Online PvPOnline | Co-opCross-Platform Multiplayer Steam | Achievements Steam Trading | Cards In-App Purchases Partial | Controller Support Remote | Play on | Phone Remote Play | on Tablet Requires | 3rd-Party Account: Xbox | Live (Supports Linking | to Steam 359550 Single-playerOnline PvPOnline | Co-opSteam Trading | Cards In-App Purchases Partial | Controller Support Remote | Play on | Phone Remote Play | on Tablet Requires | 3rd-Party Account: Ubisoft | Account (Supports Linking | to Steam | Account)Requires agreement | to a | 3rd-party EULATom | Clancy's Rainbow | Six® Siege 570 Steam Trading | Cards Steam Workshop SteamVR | Collectibles In-App Purchases Valve | Anti-Cheat enabled 230410 Single-playerSteam Trading | Cards In-App Purchases Partial | Controller Support Remote | Play on | Phone Remote Play | on Tablet Requires | 3rd-Party Account: Warframe 306130 MMOSteam Trading | Cards Partial Controller | Support Remote Play | on Tablet Requires | 3rd-Party Account: Elder | Scrolls Online | Account (Supports Linking | to Steam 238960 Single-playerMMOOnline PvPSteam | Achievements Steam Trading | Cards In-App Purchases Remote | Play on | Tablet Requires agreement | to a | 3rd-party EULAPath | of Exile | EULA 1 397540 Single-playerOnline Co-opLAN | Co-opCross-Platform Multiplayer Steam | Achievements Full controller | supportSteam Trading | Cards Steam Cloud Remote | Play on | Phone Remote Play | on Tablet Remote | Play on | TVIncorporates 3rd-party | DRM: Denuvo | Anti-tamper5 Activations | per 24 | hours machine | activation limitRequires 1129580 Single-playerFull controller 381210 Online PvPOnline | Co-opSteam Achievements Full | controller supportSteam | Trading Cards Steam | Cloud Remote Play | on Phone Remote | Play on | Tablet Remote Play | on TVRequires | agreement to | a 3rd-party | EULADead by | Daylight EULA 1250410 Single-playerSteam Achievements Full | controller supportIn-App | Purchases Requires 3rd-Party | Account: Xbox Live  271590 Single-playerSteam Achievements Full | controller supportRemote | Play on | Phone Remote Play | on Tablet Remote | Play on | TVRequires 3rd-Party | Account: Rockstar Games | Social Club  39210 Single-playerMMOOnline PvPOnline | Co-opCross-Platform Multiplayer Partial | Controller Support Remote | Play on 582660 MMOOnline PvPOnline | Co-opSteam Trading | Cards In-App Purchases Partial | Controller Support Requires | 3rd-Party Account: Black | Desert Online  412020 Single-playerSteam Achievements Full | controller supportSteam | Trading Cards Steam | Cloud Remote Play | on Phone Remote | Play on | Tablet Remote Play | on TVRequires | agreement to | a 3rd-party | EULAMetro Exodus 440900 Single-playerOnline PvPOnline | Co-opSteam Achievements Full | controller supportSteam | Trading Cards Steam | Workshop Remote Play | on Tablet Remote | Play on | TVRequires agreement | to a | 3rd-party EULAConan | Exiles EULA 236390 Single-playerMMOCross-Platform Multiplayer Steam | Achievements In-App Purchases Partial | Controller Support

In [0]:

df_category.write.csv('/mnt/bronze/steam_category_bronze.csv',
                        mode='overwrite',
                        header=True)

In [0]:

schema_pegi = StructType([
    StructField('url_info', StructType([
        StructField('id', StringType(), True),
        StructField('type', StringType(), True) 
    ]), True),
    StructField('pegi', StructType([
        StructField('age_limit', StringType(), True),
        StructField('pegi_tags', ArrayType(StringType()), True)
    ]), True),
])

df_pegi = spark.read.json("dbfs:/FileStore/tables/SteamProject/steam_data.json",
                            schema=schema_pegi)

In [0]:

# Removendo valores nulls
df_pegi = df_pegi.where(df_pegi.url_info.isNotNull())

# Desfazendo Struct em novas colunas
df_pegi = df_pegi.select(
    '*',
    col('url_info.id').alias('id')
).drop('url_info')

df_pegi = df_pegi.select(
    '*',
    col('pegi.age_limit').alias('age_limit'),
    col('pegi.pegi_tags').alias('pegi_tags')
).drop('pegi')

In [0]:

# Concatenando o array 
df_pegi = df_pegi.withColumn(
    'pegi_tags', 
    concat_ws('| ', col('pegi_tags')))

In [0]:
display(df_pegi)

id age_limit pegi_tags 945360 null 730 null 1097150 null 1158310 m Blood| LanguagePartial| Nudity| Sexual| Themes| Use| of| Drugs| Violence 1085660 m Blood| Language| Violence 1145360 null 1172620 m Violence| Use| of| Alcohol| Crude| Humor 359550 m Blood| Drug| Reference| Strong| Language| Violence 570 null 230410 m Violence,| Blood 306130 m Blood| and| Gore| Sexual| Themes| Use| of| Alcohol| Violence 238960 null 397540 m Blood| and| Gore| Intense| Violence| Sexual| Themes| Strong| Language 1129580 null 381210 m Blood| and| Gore| Intense| Violence| Strong| Language 1250410 null 271590 m Intense| Violence| Blood| and| Gore| NudityMature| Humor| Strong| Language| Strong| Sexual| Content| Use| of| Drugs| and| Alcohol 39210 m Language| Sexual| Themes| Partial| Nudity| Use| of| Alcohol| and| Tobacco| ViolenceBlood 582660 null 412020 m Blood| and| Gore,| Intense| Violence,| Partial| Nudity,| Sexual| Themes,| Strong| Language,| Use| of| Drugs 440900 null 236390 null 548430 null 252490 null 971996 null 440 null 976730 m Blood| and| Gore| ViolenceLanguage 945360 null 730 null 1097150 null 1158310 m Blood| LanguagePartial| Nudity| Sexual| Themes| Use| of| Drugs| Violence 1085660 m Blood| Language| Violence 1145360 null 1172620 m Violence| Use| of| Alcohol| Crude| Humor 359550 m Blood| Drug| Reference| Strong| Language| Violence 570 null 230410 m Violence,| Blood 306130 m Blood| and| Gore| Sexual| Themes| Use| of| Alcohol| Violence 238960 null 397540 m Blood| and| Gore| Intense| Violence| Sexual| Themes| Strong| Language 1129580 null 381210 m Blood| and| Gore| Intense| Violence| Strong| Language 1250410 null 271590 m Intense| Violence| Blood| and| Gore| NudityMature| Humor| Strong| Language| Strong| Sexual| Content| Use| of| Drugs| and| Alcohol 39210 m Language| Sexual| Themes| Partial| Nudity| Use| of| Alcohol| and| Tobacco| ViolenceBlood 582660 null 412020 m Blood| and| Gore,| Intense| Violence,| Partial| Nudity,| Sexual| Themes,| Strong| Language,| Use| of| Drugs 440900 null 236390 null 548430 null 252490 null 971996 null 440 null 976730 m Blood| and| Gore| ViolenceLanguage 1056640 m Blood| Partial| Nudity| Strong| Language| ViolenceInteractive| Elements| In-Game| Purchases 1174180 m Blood| and| Gore| Intense| Violence| NuditySexual| Content| Strong| Language| Use| of| Drugs| and| Alcohol| Interactive| Elements| In-Game| Purchases| Users| Interact 289070 m Drug| Reference| LanguageMild| Violence| Suggestive| Themes 386360 m Alcohol| Reference| Fantasy| Violence| Blood 1307550 null 582010 m Blood| Mild| Language| Use| of| Alcohol| Violence 275850 m Fantasy| Violence| Animated| Blood 1041720 m Blood| and| Gore| Intense| Violence| Suggestive| Themes 997070 m Language| Mild| Blood| Violence 632360 m Blood| Drug| Reference| Fantasy| Violence| Interactive| Elements| Users| Interact 962130 m Blood| ViolenceLanguage| Interactive| Elements| Users| Interact 629760 null 1151640 m Blood| Drug| Reference| LanguageMild| Sexual| Themes| Violence 221100 m Intense| Violence| Blood 427520 null 1222670 m Violence| Sexual| Themes| Crude| Humor 1286830 m Blood| and| Gore| Mild| Language| Sexual| Themes| ViolenceInteractive| Elements| In-Game| Purchases 489830 m Blood| and| Gore,| Intense| Violence,| Sexual| Themes,| Use| of| Alcohol 1016120 null 346110 m Blood| Crude| Humor| Use| of| Alcohol| Violence 1206200 null 526870 null 945360 null 730 null 1097150 null 1158310 m Blood| LanguagePartial| Nudity| Sexual| Themes| Use| of| Drugs| Violence 1085660 m Blood| Language| Violence 1145360 null 1172620 m Violence| Use| of| Alcohol| Crude| Humor 359550 m Blood| Drug| Reference| Strong| Language| Violence 570 null 230410 m Violence,| Blood 306130 m Blood| and| Gore| Sexual| Themes| Use| of| Alcohol| Violence 238960 null 397540 m Blood| and| Gore| Intense| Violence| Sexual| Themes| Strong| Language 1129580 null 381210 m Blood| and| Gore| Intense| Violence| Strong| Language 1250410 null 271590 m Intense| Violence| Blood| and| Gore| NudityMature| Humor| Strong| Lang

In [0]:
df_pegi.write.csv('/mnt/bronze/steam_pegi_bronze.csv',
                        mode='overwrite',
                        header=True)